# Bronze to Silver - ETL into a Silver table

We need to perform some transformations on the data to move it from bronze to silver tables.

## Step Configuration

In [0]:
%run ./includes/configuration_jsonmoive

Out[415]: DataFrame[]

### Display the Files in the Bronze Paths

In [0]:
display(dbutils.fs.ls(bronzePath))

path name size modificationTime dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/bronze/_delta_log/ _delta_log/ 0 1661397619000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/bronze/p_Ingestdate=2022-08-25/ p_Ingestdate=2022-08-25/ 0 1661397617000

## Create the rawDF DataFrame

**Note**: Use the function `read_batch_raw` to ingest the newly arrived

In [0]:
rawDF = read_batch_raw("/FileStore/tables/")
rawDF.show(10)

+--------------------+--------------------+
 movie| Movies|
+--------------------+--------------------+
[{"Id":1,"Title":...|{"Id":1,"Title":"...|
[{"Id":1,"Title":...|{"Id":2,"Title":"...|
[{"Id":1,"Title":...|{"Id":3,"Title":"...|
[{"Id":1,"Title":...|{"Id":4,"Title":"...|
[{"Id":1,"Title":...|{"Id":5,"Title":"...|
[{"Id":1,"Title":...|{"Id":6,"Title":"...|
[{"Id":1,"Title":...|{"Id":7,"Title":"...|
[{"Id":1,"Title":...|{"Id":8,"Title":"...|
[{"Id":1,"Title":...|{"Id":9,"Title":"...|
[{"Id":1,"Title":...|{"Id":10,"Title":...|
+--------------------+--------------------+
only showing top 10 rows

In [0]:
transformedRawDF = transform_raw(rawDF)
display(transformedRawDF)

Movies Ingesttime Status p_Ingestdate {"Id":1,"Title":"Inception","Overview":"Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: \"inception\", the implantation of another person's idea into a target's subconscious.","Tagline":"Your mind is the scene of the crime.","Budget":1.6E8,"Revenue":8.25532764E8,"ImdbUrl":"https://www.imdb.com/title/tt1375666","TmdbUrl":"https://www.themoviedb.org/movie/27205","PosterUrl":"https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg","OriginalLanguage":"en","ReleaseDate":"2010-07-15T00:00:00","RunTime":148,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":1,"name":"Adventure"},{"id":6,"name":"Action"},{"id":13,"name":"Science Fiction"}]} 2022-08-25T03:21:39.747+0000 New 2022-08-25 {"Id":2,"Title":"Interstellar","Overview":"The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage.","Tagline":"Mankind was born on Earth. It was never meant to die here.","Budget":1.65E8,"Revenue":6.75120017E8,"ImdbUrl":"https://www.imdb.com/title/tt0816692","TmdbUrl":"https://www.themoviedb.org/movie/157336","PosterUrl":"https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg","OriginalLanguage":"en","ReleaseDate":"2014-11-05T00:00:00","RunTime":169,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":1,"name":"Adventure"},{"id":4,"name":"Drama"},{"id":13,"name":"Science Fiction"}]} 2022-08-25T03:21:39.747+0000 New 2022-08-25 {"Id":3,"Title":"The Dark Knight","Overview":"Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker.","Tagline":"Why So Serious?","Budget":1.85E8,"Revenue":1.004558444E9,"ImdbUrl":"https://www.imdb.com/title/tt0468569","TmdbUrl":"https://www.themoviedb.org/movie/155","PosterUrl":"https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg","OriginalLanguage":"en","ReleaseDate":"2008-07-16T00:00:00","RunTime":152,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":4,"name":"Drama"},{"id":6,"name":"Action"},{"id":10,"name":"Thriller"},{"id":11,"name":"Crime"}]} 2022-08-25T03:21:39.747+0000 New 2022-08-25 {"Id":4,"Title":"Deadpool","Overview":"Deadpool tells the origin story of former Special Forces operative turned mercenary Wade Wilson, who after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts the alter ego Deadpool. Armed with his new abilities and a dark, twisted sense of humor, Deadpool hunts down the man who nearly destroyed his life.","Tagline":"Witness the beginning of a happy ending","Budget":5.8E7,"Revenue":7.831E8,"ImdbUrl":"https://www.imdb.com/title/tt1431045","TmdbUrl":"https://www.themoviedb.org/movie/293660","PosterUrl":"https://image.tmdb.org/t/p/w342//yGSxMiF0cYuAiyuve5DA6bnWEOI.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//en971MEXui9diirXlogOrPKmsEn.jpg","OriginalLanguage":"en","ReleaseDate":"2016-02-09T00:00:00","RunTime":108,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":n

## Verify the Schema with an Assertion

In [0]:
from pyspark.sql.types import *

assert transformedRawDF.schema == StructType(
    [
        StructField("Movies", StringType(), True),
        StructField("Ingesttime", TimestampType(), False),
        StructField("Status", StringType(), False),
        StructField("p_Ingestdate", DateType(), False),
    ]
)
print("Assertion passed.")

Assertion passed.

### Write Batch to a Bronze Table

**Note**: you will need to begin the write with the `.save()` method on
your writer.

          Use the function `batch_writer` to ingest the newly arrived

**Be sure to partition on `p_ingestdate`**.

In [0]:
rawToBronzeWriter = batch_writer(
    dataframe=transformedRawDF, partition_column="p_ingestdate"
)

rawToBronzeWriter.save(bronzePath)

In [0]:
display(dbutils.fs.ls(bronzePath))

path name size modificationTime dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/bronze/_delta_log/ _delta_log/ 0 1661397715000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/bronze/p_Ingestdate=2022-08-25/ p_Ingestdate=2022-08-25/ 0 1661397710000

## Display the Bronze Table

In [0]:
%sql
SELECT * FROM movies_df_bronze

Movies Ingesttime Status p_Ingestdate {"Id":1,"Title":"Inception","Overview":"Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: \"inception\", the implantation of another person's idea into a target's subconscious.","Tagline":"Your mind is the scene of the crime.","Budget":1.6E8,"Revenue":8.25532764E8,"ImdbUrl":"https://www.imdb.com/title/tt1375666","TmdbUrl":"https://www.themoviedb.org/movie/27205","PosterUrl":"https://image.tmdb.org/t/p/w342//9gk7adHYeDvHkCSEqAvQNLV5Uge.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//s3TBrRGB1iav7gFOCNx3H31MoES.jpg","OriginalLanguage":"en","ReleaseDate":"2010-07-15T00:00:00","RunTime":148,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":1,"name":"Adventure"},{"id":6,"name":"Action"},{"id":13,"name":"Science Fiction"}]} 2022-08-25T03:21:50.009+0000 New 2022-08-25 {"Id":2,"Title":"Interstellar","Overview":"The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage.","Tagline":"Mankind was born on Earth. It was never meant to die here.","Budget":1.65E8,"Revenue":6.75120017E8,"ImdbUrl":"https://www.imdb.com/title/tt0816692","TmdbUrl":"https://www.themoviedb.org/movie/157336","PosterUrl":"https://image.tmdb.org/t/p/w342//gEU2QniE6E77NI6lCU6MxlNBvIx.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//xJHokMbljvjADYdit5fK5VQsXEG.jpg","OriginalLanguage":"en","ReleaseDate":"2014-11-05T00:00:00","RunTime":169,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":1,"name":"Adventure"},{"id":4,"name":"Drama"},{"id":13,"name":"Science Fiction"}]} 2022-08-25T03:21:50.009+0000 New 2022-08-25 {"Id":3,"Title":"The Dark Knight","Overview":"Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker.","Tagline":"Why So Serious?","Budget":1.85E8,"Revenue":1.004558444E9,"ImdbUrl":"https://www.imdb.com/title/tt0468569","TmdbUrl":"https://www.themoviedb.org/movie/155","PosterUrl":"https://image.tmdb.org/t/p/w342//qJ2tW6WMUDux911r6m7haRef0WH.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//hkBaDkMWbLaf8B1lsWsKX7Ew3Xq.jpg","OriginalLanguage":"en","ReleaseDate":"2008-07-16T00:00:00","RunTime":152,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":4,"name":"Drama"},{"id":6,"name":"Action"},{"id":10,"name":"Thriller"},{"id":11,"name":"Crime"}]} 2022-08-25T03:21:50.009+0000 New 2022-08-25 {"Id":4,"Title":"Deadpool","Overview":"Deadpool tells the origin story of former Special Forces operative turned mercenary Wade Wilson, who after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts the alter ego Deadpool. Armed with his new abilities and a dark, twisted sense of humor, Deadpool hunts down the man who nearly destroyed his life.","Tagline":"Witness the beginning of a happy ending","Budget":5.8E7,"Revenue":7.831E8,"ImdbUrl":"https://www.imdb.com/title/tt1431045","TmdbUrl":"https://www.themoviedb.org/movie/293660","PosterUrl":"https://image.tmdb.org/t/p/w342//yGSxMiF0cYuAiyuve5DA6bnWEOI.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//en971MEXui9diirXlogOrPKmsEn.jpg","OriginalLanguage":"en","ReleaseDate":"2016-02-09T00:00:00","RunTime":108,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.1633333","UpdatedDate":null,"UpdatedBy":n

In [0]:
%sql
select count(Status) from movies_df_bronze

count(Status) 9995

## Bronze to Silver Step

Let's start the Bronze to Silver step.

## Load New Records from the Bronze Records

**EXERCISE**

Load all records from the Bronze table with a status of `"new"`.

In [0]:
bronzeDF = spark.read.table("movies_df_bronze").filter("Status = 'New'")

## Extract the Nested JSON from the Bronze Records

### Step 1: Extract the Nested JSON from the `value` column
**EXERCISE**

Use `pyspark.sql` functions to extract the `"value"` column as a new
column `"nested_json"`.

In [0]:
bronzeDF.show()

+--------------------+--------------------+------+------------+
 Movies| Ingesttime|Status|p_Ingestdate|
+--------------------+--------------------+------+------------+
{"Id":1,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":2,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":3,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":4,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":5,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":6,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":7,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":8,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":9,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":10,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":11,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":12,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":13,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":14,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":15,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":16,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":17,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":18,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":19,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
{"Id":20,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|
+--------------------+--------------------+------+------------+
only showing top 20 rows

In [0]:
bronzeDF.count()

Out[436]: 9995

In [0]:
bronzeDF.dtypes

Out[441]: [('Movies', 'string'),
 ('Ingesttime', 'timestamp'),
 ('Status', 'string'),
 ('p_Ingestdate', 'date')]

In [0]:
from pyspark.sql.functions import from_json

json_schema = """
    Id LONG,
    Title STRING,      
    Overview STRING,
    OriginalLanguage STRING,
    Price DOUBLE,
    ReleaseDate TIMESTAMP,
    Budget DOUBLE,
    Revenue DOUBLE,
    RunTime LONG,
    Tagline STRING,
    genres ARRAY<STRING>,
    CreatedBy STRING,
    CreatedDate TIMESTAMP,
    UpdatedBy STRING,
    UpdatedDate TIMESTAMP,
    ImdbUrl STRING,
    TmdbUrl STRING,
    PosterUrl STRING,
    BackdropUrl STRING
"""

bronzeAugmentedDF = bronzeDF.withColumn("nested_json", from_json(col("Movies"), json_schema))

In [0]:
bronzeAugmentedDF.show()

+--------------------+--------------------+------+------------+--------------------+
 Movies| Ingesttime|Status|p_Ingestdate| nested_json|
+--------------------+--------------------+------+------------+--------------------+
{"Id":1,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{1, Inception, Co...|
{"Id":2,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{2, Interstellar,...|
{"Id":3,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{3, The Dark Knig...|
{"Id":4,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{4, Deadpool, Dea...|
{"Id":5,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{5, The Avengers,...|
{"Id":6,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{6, Avatar, In th...|
{"Id":7,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{7, Guardians of ...|
{"Id":8,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{8, Fight Club, A...|
{"Id":9,"Title":"...|2022-08-25 03:21:...| New| 2022-08-25|{9, Avengers: Inf...|
{"Id":10,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{10, Pulp Fiction...|
{"Id":11,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{11, Django Uncha...|
{"Id":12,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{12, Iron Man, Af...|
{"Id":13,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{13, Forrest Gump...|
{"Id":14,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{14, Harry Potter...|
{"Id":15,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{15, The Matrix, ...|
{"Id":16,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{16, Titanic, 101...|
{"Id":17,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{17, The Lord of ...|
{"Id":18,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{18, The Shawshan...|
{"Id":19,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{19, Mad Max: Fur...|
{"Id":20,"Title":...|2022-08-25 03:21:...| New| 2022-08-25|{20, Captain Amer...|
+--------------------+--------------------+------+------------+--------------------+
only showing top 20 rows

In [0]:
bronzeAugmentedDF.count()

Out[475]: 9995

### Step 2: Create the Silver DataFrame by Unpacking the `nested_json` Column

Unpacking a JSON column means to flatten the JSON and include each top level attribute
as its own column.

🚨 **IMPORTANT** Be sure to include the `"Movies"` column in the Silver DataFrame
because we will later use it as a unique reference to each record in the
Bronze table

In [0]:
movies_df_silver = bronzeAugmentedDF.select("Movies", "nested_json.*")

## Verify the Schema with an Assertion

In [0]:
from pyspark.sql.types import _parse_datatype_string

assert movies_df_silver.schema == _parse_datatype_string(
    """
    Movies STRING,
    Id LONG,
    Title STRING,      
    Overview STRING,
    OriginalLanguage STRING,
    Price DOUBLE,
    ReleaseDate TIMESTAMP,
    Budget DOUBLE,
    Revenue DOUBLE,
    RunTime LONG,
    Tagline STRING,
    genres ARRAY<STRING>,
    CreatedBy STRING,
    CreatedDate TIMESTAMP,
    UpdatedBy STRING,
    UpdatedDate TIMESTAMP,
    ImdbUrl STRING,
    TmdbUrl STRING,
    PosterUrl STRING,
    BackdropUrl STRING
"""
)
print("Assertion passed.")

Assertion passed.

## Transform the Data

💪🏼 Remember that we name the new column `p_eventdate` to indicate
that we are partitioning on this column.

🕵🏽‍♀️ Remember that we are keeping the `Movies` as a unique reference to values
in the Bronze table.

In [0]:
from pyspark.sql.functions import col

movies_df_silver = movies_df_silver.select(
    'Movies',
    'Id',
    'Title',
    'Overview',
    'OriginalLanguage',
    'Price',
    'ReleaseDate',
    col('ReleaseDate').cast('date').alias('p_ReleaseDate'),
    'Budget',
    'Revenue',
    'RunTime',
    'Tagline',
    'genres',
    'CreatedBy',
    'CreatedDate',
    'UpdatedBy',
    'UpdatedDate',
    'ImdbUrl',
    'TmdbUrl',
    'PosterUrl',
    'BackdropUrl'
)

## Verify the Schema with an Assertion

💪🏼 Remember, the function `_parse_datatype_string` converts a DDL format schema string into a Spark schema.

In [0]:
from pyspark.sql.types import _parse_datatype_string

assert movies_df_silver.schema == _parse_datatype_string(
    """
    Movies STRING,
    Id LONG,
    Title STRING,      
    Overview STRING,
    OriginalLanguage STRING,
    Price DOUBLE,
    ReleaseDate TIMESTAMP,
    p_ReleaseDate DATE,
    Budget DOUBLE,
    Revenue DOUBLE,
    RunTime LONG,
    Tagline STRING,
    genres ARRAY<STRING>,
    CreatedBy STRING,
    CreatedDate TIMESTAMP,
    UpdatedBy STRING,
    UpdatedDate TIMESTAMP,
    ImdbUrl STRING,
    TmdbUrl STRING,
    PosterUrl STRING,
    BackdropUrl STRING
"""
), "Schemas do not match"
print("Assertion passed.")

Assertion passed.

## Quarantine the Bad Data

Recall that at step, `00_ingest_raw`, we identified that some records were coming in
with device_ids passed as uuid strings instead of string-encoded integers.
Our Silver table stores device_ids as integers so clearly there is an issue
with the incoming data.

In order to properly handle this data quality issue, we will quarantine
the bad records for later processing.

Check for records that have nulls - compare the output of the following two cells

In [0]:
movies_df_silver.count()

Out[480]: 9995

In [0]:
movies_df_silver.na.drop().count()

Out[481]: 0

### Split the Silver DataFrame

In [0]:
movies_df_silver_clean = movies_df_silver.filter("Id IS NOT NULL AND ReleaseDate IS NOT NULL AND RUNTIME > 0")
movies_df_silver_quarantine = movies_df_silver.filter("Id IS NULL OR ReleaseDate IS NULL OR RUNTIME < 0")

In [0]:
movies_df_silver_clean = movies_df_silver_clean.dropDuplicates()

In [0]:
movies_df_silver_clean.count()

Out[498]: 9976

### Display the Quarantined Records

In [0]:
movies_df_silver_quarantine = movies_df_silver_quarantine.dropDuplicates()

In [0]:
display(movies_df_silver_quarantine)

Movies Id Title Overview OriginalLanguage Price ReleaseDate p_ReleaseDate Budget Revenue RunTime Tagline genres CreatedBy CreatedDate UpdatedBy UpdatedDate ImdbUrl TmdbUrl PosterUrl BackdropUrl {"Id":8762,"Title":"Permission","Overview":"A woman on the brink of a marriage proposal is told by a friend that she should date other men before spending the rest of her life with her boyfriend.","Tagline":"How can you be certain he is the one, if he is the only one?","Budget":0.0,"Revenue":0.0,"ImdbUrl":"https://www.imdb.com/title/tt5390066","TmdbUrl":"https://www.themoviedb.org/movie/390059","PosterUrl":"https://image.tmdb.org/t/p/w342//1YIGIS0Imzi5S2bbkjlQOhEJthS.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//9XT13CpZWrnpcot8DCBupulkTVo.jpg","OriginalLanguage":"en","ReleaseDate":"2017-04-22T00:00:00","RunTime":-96,"Price":9.9,"CreatedDate":"2021-04-03T16:51:31.5666667","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":4,"name":"Drama"},{"id":7,"name":"Comedy"},{"id":16,"name":"Romance"}]} 8762 Permission A woman on the brink of a marriage proposal is told by a friend that she should date other men before spending the rest of her life with her boyfriend. en 9.9 2017-04-22T00:00:00.000+0000 2017-04-22 0.0 0.0 -96 How can you be certain he is the one, if he is the only one? List({"id":4,"name":"Drama"}, {"id":7,"name":"Comedy"}, {"id":16,"name":"Romance"}) null 2021-04-03T16:51:31.566+0000 null null https://www.imdb.com/title/tt5390066 https://www.themoviedb.org/movie/390059 https://image.tmdb.org/t/p/w342//1YIGIS0Imzi5S2bbkjlQOhEJthS.jpg https://image.tmdb.org/t/p/original//9XT13CpZWrnpcot8DCBupulkTVo.jpg {"Id":2516,"Title":"Astro Boy","Overview":"Set in the futuristic Metro City, Astro Boy (Atom) is a young robot with incredible powers created by a brilliant scientist in the image of the son he had lost. Unable to fulfill his creator's expectations, Astro embarks on a journey in search of acceptance, experiencing betrayal and a netherworld of robot gladiators, before returning to save Metro City and reconcile with the father who rejected him.","Tagline":"Have a blast.","Budget":1.0E7,"Revenue":1.9551067E7,"ImdbUrl":"https://www.imdb.com/title/tt0375568","TmdbUrl":"https://www.themoviedb.org/movie/16577","PosterUrl":"https://image.tmdb.org/t/p/w342//fYOJaaCpqq1NatziVJntmsXXDi8.jpg","BackdropUrl":"https://image.tmdb.org/t/p/original//qXD5vfFe1blOXJbOHXlU5CYJMQB.jpg","OriginalLanguage":"en","ReleaseDate":"2009-10-15T00:00:00","RunTime":-94,"Price":9.9,"CreatedDate":"2021-04-03T16:51:30.6600000","UpdatedDate":null,"UpdatedBy":null,"CreatedBy":null,"genres":[{"id":3,"name":"Animation"},{"id":6,"name":"Action"},{"id":13,"name":"Science Fiction"},{"id":17,"name":"Family"}]} 2516 Astro Boy Set in the futuristic Metro City, Astro Boy (Atom) is a young robot with incredible powers created by a brilliant scientist in the image of the son he had lost. Unable to fulfill his creator's expectations, Astro embarks on a journey in search of acceptance, experiencing betrayal and a netherworld of robot gladiators, before returning to save Metro City and reconcile with the father who rejected him. en 9.9 2009-10-15T00:00:00.000+0000 2009-10-15 1.0E7 1.9551067E7 -94 Have a blast. List({"id":3,"name":"Animation"}, {"id":6,"name":"Action"}, {"id":13,"name":"Science Fiction"}, {"id":17,"name":"Family"}) null 2021-04-03T16:51:30.660+0000 null null https://www.imdb.com/title/tt0375568 https://www.themoviedb.org/movie/16577 https://image.tmdb.org/t/p/w342//fYOJaaCpqq1NatziVJntmsXXDi8.jpg https://image.tmdb.org/t/p/original//qXD5vfFe1blOXJbOHXlU5CYJMQB.jpg {"Id":5008,"Title":"D.E.B.S.","Overview":"The star of a team of teenage crime fighters falls for the alluring villainess she must bring to justice.","Tagline":"Evil is so totally busted!","Budget":3500000.0,"Revenue":0.0,"ImdbUrl":"https://www.imdb.com/title/tt0367631","TmdbUrl":"https://www.themoviedb.org/movie/540","PosterUrl":"https://image.tmdb.org/t/p/w342//cMwLTcG5aVBYeh5W6S

## WRITE Clean Batch to a Silver Table

**EXERCISE:** Batch write `movies_df_silver_clean` to the Silver table path, `silverPath`.

1. Use format, `"delta"`
1. Use mode `"append"`.
1. Do **NOT** include the `Movies` column.
1. Partition by `"p_Releasedate"`.

In [0]:
(
    movies_df_silver_clean.select(
    'Id',
    'Title',
    'Overview',
    'OriginalLanguage',
    'Price',
    'ReleaseDate',
    'p_ReleaseDate',
    'Budget',
    'Revenue',
    'RunTime',
    'Tagline',
    'genres',
    'CreatedBy',
    'CreatedDate',
    'UpdatedBy',
    'UpdatedDate',
    'ImdbUrl',
    'TmdbUrl',
    'PosterUrl',
    'BackdropUrl'
    )
    .write.format("delta")
    .mode("append")
    .partitionBy("p_ReleaseDate")
    .save(silverPath)
)

In [0]:
display(dbutils.fs.ls(silverPath))

path name size modificationTime dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/_delta_log/ _delta_log/ 0 1661400539000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1903-12-07/ p_ReleaseDate=1903-12-07/ 0 1661400217000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1910-03-18/ p_ReleaseDate=1910-03-18/ 0 1661400217000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1914-02-08/ p_ReleaseDate=1914-02-08/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1915-02-08/ p_ReleaseDate=1915-02-08/ 0 1661400217000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1916-07-10/ p_ReleaseDate=1916-07-10/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1916-09-04/ p_ReleaseDate=1916-09-04/ 0 1661400217000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1917-01-22/ p_ReleaseDate=1917-01-22/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1917-06-17/ p_ReleaseDate=1917-06-17/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1918-04-14/ p_ReleaseDate=1918-04-14/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1918-10-20/ p_ReleaseDate=1918-10-20/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1919-05-13/ p_ReleaseDate=1919-05-13/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1920-08-29/ p_ReleaseDate=1920-08-29/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1921-01-21/ p_ReleaseDate=1921-01-21/ 0 1661400217000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1922-03-15/ p_ReleaseDate=1922-03-15/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1922-06-11/ p_ReleaseDate=1922-06-11/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1923-04-01/ p_ReleaseDate=1923-04-01/ 0 1661400217000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1923-10-01/ p_ReleaseDate=1923-10-01/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1923-11-19/ p_ReleaseDate=1923-11-19/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1924-04-17/ p_ReleaseDate=1924-04-17/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1924-09-28/ p_ReleaseDate=1924-09-28/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1925-01-26/ p_ReleaseDate=1925-01-26/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1925-03-15/ p_ReleaseDate=1925-03-15/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1925-07-12/ p_ReleaseDate=1925-07-12/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1925-09-22/ p_ReleaseDate=1925-09-22/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1926-12-25/ p_ReleaseDate=1926-12-25/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1927-02-14/ p_ReleaseDate=1927-02-14/ 0 1661400218000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1927-05-29/ p_ReleaseDate=1927-05-29/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1927-08-12/ p_ReleaseDate=1927-08-12/ 0 1661400219000 dbfs:/dbacademy/sheng_lu_jsonMoive/jsonmoivepractice/movie/silver/p_ReleaseDate=1927-10-06/ p_ReleaseDate=1927

In [0]:
spark.sql(
    """
DROP TABLE IF EXISTS movies_df_silver
"""
)

spark.sql(
    f"""
CREATE TABLE movies_df_silver
USING DELTA
LOCATION "{silverPath}"
"""
)

Out[493]: DataFrame[]

## Verify the Schema with an Assertion

In [0]:
silverTable = spark.read.table("movies_df_silver")
expected_schema = """
    Id LONG,
    Title STRING,      
    Overview STRING,
    OriginalLanguage STRING,
    Price DOUBLE,
    ReleaseDate TIMESTAMP,
    p_ReleaseDate DATE,
    Budget DOUBLE,
    Revenue DOUBLE,
    RunTime LONG,
    Tagline STRING,
    genres ARRAY<STRING>,
    CreatedBy STRING,
    CreatedDate TIMESTAMP,
    UpdatedBy STRING,
    UpdatedDate TIMESTAMP,
    ImdbUrl STRING,
    TmdbUrl STRING,
    PosterUrl STRING,
    BackdropUrl STRING
"""

assert silverTable.schema == _parse_datatype_string(
    expected_schema
), "Schemas do not match"
print("Assertion passed.")

Assertion passed.

In [0]:
%sql

SELECT * FROM movies_df_silver

Id Title Overview OriginalLanguage Price ReleaseDate p_ReleaseDate Budget Revenue RunTime Tagline genres CreatedBy CreatedDate UpdatedBy UpdatedDate ImdbUrl TmdbUrl PosterUrl BackdropUrl 9703 Gothic The year is 1816. A sprawling villa in Switzerland is the setting for a stormy night of madness. On this night of the "Haunted Summer," five famous friends gather around an ancient skull to conjure up their darkest fears. Poets Lord Byron and Percy Shelley, Shelley's fiancée Mary Godwin, Mary's stepsister Claire Clairemont and Byron's friend John Polidori spend a hallucinogenic evening confronting their fears in a frenzy of shocking lunacy. Horrifying visions invade the castle - realizations of Byron's fear of leeches, Shelley's fear of premature burial, Mary's fear of birthing a stillborn child - all brought forth in a bizarre dreamscape. They share the terrifying fantasies that chase them through the castle that night. The events of that night later inspired Mary Shelley to write the classic "Frankenstein" and Dr. Polidori to pen "The Vampyre," which became the basis for the creation of Dracula.. en 9.9 1986-11-30T00:00:00.000+0000 1986-11-30 0.0 0.0 84 Conjure up your deepest, darkest fear... now call that fear to life. List({"id":2,"name":"Fantasy"}, {"id":4,"name":"Drama"}, {"id":5,"name":"Horror"}, {"id":8,"name":"History"}) null 2021-04-03T16:51:31.700+0000 null null https://www.imdb.com/title/tt0091142 https://www.themoviedb.org/movie/33516 https://image.tmdb.org/t/p/w342//xGXj6wpJimmWkQMahZryM7xB9EX.jpg https://image.tmdb.org/t/p/original//itG5rMUHXC1GZzXEjVS5XpTI1iH.jpg 8331 Saturn 3 In the future, Earth is overcrowded and the population relies on distant bases to be fed. In the Saturn 3 station, Major Adam and the scientist Alex, who is also his lover and has never been on Earth, have been researching hydroponics for three years in the base alone with their dog Sally. Meanwhile, the psychotic Captain Benson fails the mental test required to travel to Saturn 3 and kills his replacement, Captain James, taking his place in the mission of assembling and programming the Demi-God series robot Hector to replace one of the scientists in Saturn 3. On the arrival, the mentally disturbed Captain Benson becomes sexually obsessed for Alex. Then he uses an interface to link his brain to program Hector, but incapable to control his emotions, he transfers his homicidal tendency and insanity to Hector. Now Major Adam and Alex are trapped in the station with a dangerous psychopath robot. en 9.9 1980-02-15T00:00:00.000+0000 1980-02-15 0.0 0.0 95 Some thing is watching... waiting... and wanting on... List({"id":10,"name":"Thriller"}, {"id":13,"name":"Science Fiction"}) null 2021-04-03T16:51:31.510+0000 null null https://www.imdb.com/title/tt0079285 https://www.themoviedb.org/movie/19761 https://image.tmdb.org/t/p/w342//zAoLR1azwd8QbglnjWpOwJ4PI6C.jpg https://image.tmdb.org/t/p/original//7CIjSIY63hPQIcQXBkkk8QtfxKl.jpg 8196 Colossus: The Forbin Project Forbin is the designer of an incredibly sophisticated computer that will run all of America's nuclear defenses. Shortly after being turned on, it detects the existence of Guardian, the Soviet counterpart, previously unknown to US Planners. Both computers insist that they be linked, and after taking safeguards to preserve confidential material, each side agrees to allow it. As soon as the link is established the two become a new Super computer and threaten the world with the immediate launch of nuclear weapons if they are detached. Colossus begins to give its plans for the management of the world under its guidance. Forbin and the other scientists form a technological resistance to Colossus which must operate underground. en 9.9 1970-04-08T00:00:00.000+0000 1970-04-08 0.0 0.0 100 This is the dawning of the Age of Colossus (where peace is compulsory... freedom is forbidden... and Man's greatest invention could be Man's greatest mistake). List({"id":10,"name":"Thriller"}, {"id":13,"name":"Science

## Update Bronze table to Reflect the Loads

**EXERCISE:** Update the records in the Bronze table to reflect updates.

### Step 1: Update Clean records
Clean records that have been loaded into the Silver table and should have
   their Bronze table `status` updated to `"loaded"`.

💃🏽 **Hint** You are matching the `Movies` column in your clean Silver DataFrame
to the `Movies` column in the Bronze table.

In [0]:
from delta.tables import DeltaTable

bronzeTable = DeltaTable.forPath(spark, bronzePath)
silverAugmented = movies_df_silver_clean.withColumn("status", lit("loaded"))

update_match = "bronze.Movies = clean.Movies"
update = {"status": "clean.status"}

(
    bronzeTable.alias("bronze")
    .merge(silverAugmented.alias("clean"), update_match)
    .whenMatchedUpdate(set=update)
    .execute()
)

**EXERCISE:** Update the records in the Bronze table to reflect updates.

### Step 2: Update Quarantined records
Quarantined records should have their Bronze table `status` updated to `"quarantined"`.

🕺🏻 **Hint** You are matching the `value` column in your quarantine Silver
DataFrame to the `value` column in the Bronze table.

In [0]:
silverAugmented = movies_df_silver_quarantine.withColumn(
    "status", lit("quarantined")
)

update_match = "bronze.Movies = quarantine.Movies"
update = {"status": "quarantine.status"}

(
    bronzeTable.alias("bronze")
    .merge(silverAugmented.alias("quarantine"), update_match)
    .whenMatchedUpdate(set=update)
    .execute()
)